### Create Lookup features 

We've learned how to define a target and materialize data using observation tables. Now, let's dive into basic feature engineering.

The most straightforward features we can craft with FeatureByte are known as lookup features. These are either direct columns taken from the source table or simple computations that don't require any aggregations.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

16:41:57 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:41:57 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:41:57 | INFO     | SDK version: 0.6.0.dev121
16:41:57 | INFO     | No catalog activated.
16:41:58 | INFO     | 11 feature lists, 66 features deployed
16:41:58 | INFO     | Using profile: tutorial
16:41:58 | INFO     | Using configuration file at: /Users/viktor/.featurebyte/config.yaml
16:41:58 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
16:41:58 | INFO     | SDK version: 0.6.0.dev121
16:41:58 | INFO     | No catalog activated.
16:41:58 | INFO     | 11 feature lists, 66 features deployed
16:41:59 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYCUSTOMER scd table.
grocerycustomer_view = catalog.get_view("GROCERYCUSTOMER")

#### Create Lookup feature

In [3]:
# Create lookup feature from DateOfBirth column for customer entity.
customer_dateofbirth = grocerycustomer_view["DateOfBirth"].as_feature("CUSTOMER_DateOfBirth")

#### Derive Age at the point-in-time of the request observation

In [4]:
# Derive Age from the point-in-time and the date of birth.
customer_age = (
    (fb.RequestColumn.point_in_time()- customer_dateofbirth).dt.day / 365.25
).floor()
# Name feature
customer_age.name = "CUSTOMER_Age"

In [5]:
# Transform age into a 5 year age band.
customer_age_band = (
    ((customer_age + 1) / 5).ceil() - 1
) * 5
customer_age_band = (
    customer_age_band.astype(str)
     + "-" + (customer_age_band + 4).astype(str)
)
# Name feature
customer_age_band.name = "CUSTOMER_Age_band"

#### Preview feature
We will use observation table we created in previous tutorial here.

In [6]:
# Check the primary entity of the feature'
customer_age.primary_entity

 {
   'name': 'customer',
   'created_at': '2023-11-27T15:39:09.477000',
   'updated_at': '2023-11-27T15:39:19.968000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [7]:
# Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table("Preview Table with 10 Customers").to_pandas()

In [8]:
# Preview CUSTOMER_Age
customer_age.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID  CUSTOMER_Age
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2            66
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9            59
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47            19
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b            70
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd            24
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0            22
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db            39
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c            85
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597            83
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301            54

In [9]:
# Preview CUSTOMER_Age_band
customer_age_band.preview(preview_table)

POINT_IN_TIME                   GROCERYCUSTOMERGUID CUSTOMER_Age_band
0 2022-11-28 11:36:31  d4559f7d-eb28-42c6-b47d-847de24952c2             65-69
1 2022-10-09 15:47:55  3f8c7c4c-f2c2-408e-a08e-622de3d3a0b9             55-59
2 2022-09-14 15:42:42  35390325-8443-43c1-a934-18db923d9a47             15-19
3 2022-12-26 18:39:46  4eb4ee84-ee13-4eec-9c26-61b6eb4ba35b             70-74
4 2022-12-06 08:47:43  e42fa5f3-7737-4c6a-9ef4-856f113e60bd             20-24
5 2022-11-09 12:14:40  8440debb-6abc-4adc-8c6c-749928141fd0             20-24
6 2022-10-12 17:32:15  8a54e527-e9a4-47a9-a28f-8b3c6ecc02db             35-39
7 2023-01-01 11:51:28  cea213d4-36e4-48c3-ae8d-c7a25911e11c             85-89
8 2023-02-05 15:48:23  3b4f2821-b761-40e9-a32a-5f09685cc597             80-84
9 2023-03-10 16:15:46  91a64566-e212-4e36-8f23-c1f1f324a301             50-54

In [10]:
# Save features to catalog 
customer_age.save()
customer_age_band.save()

Done! |████████████████████████████████████████| 100% in 6.5s (0.16%/s)         
Done! |████████████████████████████████████████| 100% in 6.5s (0.16%/s)         


In [11]:
# Add description
customer_age.update_description("Age of the customer.")
customer_age_band.update_description("Age Band of the customer.")

#### Check feature definition files (same as definition files we discussed in target tutorial)

In [12]:
customer_age.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("6564b7eabeba6c193e0fe3bb"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\noutput = feat_1\noutput.save(_id=ObjectId("6564b8c8e991187ee84de744"))\n'

In [13]:
customer_age_band.definition

'# Generated by SDK version: 0.6.0.dev121\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("6564b7eabeba6c193e0fe3bb"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\nfeat_2 = ((((feat_1 + 1) / 5).ceil() - 1) * 5) + 4\nfeat_3 = ((((feat_1 + 1) / 5).ceil() - 1) * 5).astype(str) + "-"\nfeat_4 = feat_3 + feat_2.astype(str)\nfeat_4.name = "CUSTOMER_Age_band"\noutput = feat_4\noutput.save(_id=ObjectId("6564b8c8e991187ee84de74e"))\n'

### Concepts in this tutorial
- [More on features](https://docs.featurebyte.com/latest/about/glossary/#feature-creation)
- [More on lookup features](https://docs.featurebyte.com/latest/about/glossary/#lookup-features)
- [More about point-in-time](https://docs.featurebyte.com/latest/about/glossary/#point-in-time)

#### SDK reference for
- [Feature](https://docs.featurebyte.com/latest/reference/core/feature/)
- [ViewColumn.as_feature()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.ViewColumn.as_feature/)
- [RequestColumn.point_in_time](https://docs.featurebyte.com/latest/reference/featurebyte.api.request_column.RequestColumn.point_in_time/)
- [Feature.preview()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)
- [Feature.save()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)